In [122]:
import os
import pandas as pd
import re

from kedro.pipeline import *
from kedro.io import *
from kedro.runner import *

import pickle
import os
import pandas as pd
import numpy as np
import scipy.stats as stats

In [123]:
csv_file_path = r'C:\Users\jrubio\hcl_data\data\02_intermediate\table_I_final.csv'
df = pd.read_csv(csv_file_path)
df

WEEK_LABEL DIAGNOSIS_CATEGORY           AGE_CLASS RSS_DURATION_CLASS  \
0     2023-01-02           COVID_19  65 years and older    5 days and more   
1     2023-01-09           COVID_19  65 years and older    5 days and more   
2     2023-01-16           COVID_19  65 years and older    5 days and more   
3     2023-01-23           COVID_19  65 years and older    5 days and more   
4     2023-01-30           COVID_19  65 years and older    5 days and more   
...          ...                ...                 ...                ...   
2623  2023-03-27                RSV     [50 - 65[ years       [2 - 5[ days   
2624  2023-04-03                RSV     [50 - 65[ years       [2 - 5[ days   
2625  2023-04-10                RSV     [50 - 65[ years       [2 - 5[ days   
2626  2023-04-17                RSV     [50 - 65[ years       [2 - 5[ days   
2627  2023-04-24                RSV     [50 - 65[ years       [2 - 5[ days   

      N_CASES  BASELINE_N_CASES  N_CASES_NOWCAST  N_CASES_SMOOTH  
0          42                27               42       42.000000  
1          31                27               31       36.498472  
2          23                27               23       31.996482  
3          25                27               25       30.245903  
4          16                27               16       27.393556  
...       ...               ...              ...             ...  
2623        0                 0                2        1.001481  
2624        0                 0                3        1.155727  
2625        0                 0                4        1.359623  
2626        0                 0                6        1.670186  
2627        0                 0               10        2.192972  

[2628 rows x 8 columns]

In [127]:
# Define the confidence level (e.g., 95%)
confidence_level = 0.95

# Calculate the critical value using the normal distribution
z = stats.norm.ppf((1 + confidence_level) / 2)

# Calculate the confidence interval for each BASELINE_N_CASES value
df['LOWER_CI'] = df['BASELINE_N_CASES'] - z * np.sqrt(df['BASELINE_N_CASES'])
df['UPPER_CI'] = df['BASELINE_N_CASES'] + z * np.sqrt(df['BASELINE_N_CASES'])

WEEK_LABEL DIAGNOSIS_CATEGORY           AGE_CLASS RSS_DURATION_CLASS  \
0     2023-01-02           COVID_19  65 years and older    5 days and more   
1     2023-01-09           COVID_19  65 years and older    5 days and more   
2     2023-01-16           COVID_19  65 years and older    5 days and more   
3     2023-01-23           COVID_19  65 years and older    5 days and more   
4     2023-01-30           COVID_19  65 years and older    5 days and more   
...          ...                ...                 ...                ...   
2623  2023-03-27                RSV     [50 - 65[ years       [2 - 5[ days   
2624  2023-04-03                RSV     [50 - 65[ years       [2 - 5[ days   
2625  2023-04-10                RSV     [50 - 65[ years       [2 - 5[ days   
2626  2023-04-17                RSV     [50 - 65[ years       [2 - 5[ days   
2627  2023-04-24                RSV     [50 - 65[ years       [2 - 5[ days   

      N_CASES  BASELINE_N_CASES  N_CASES_NOWCAST  N_CASES_SMOOTH      LOWER  \
0          42                27               42       42.000000  16.815728   
1          31                27               31       36.498472  16.815728   
2          23                27               23       31.996482  16.815728   
3          25                27               25       30.245903  16.815728   
4          16                27               16       27.393556  16.815728   
...       ...               ...              ...             ...        ...   
2623        0                 0                2        1.001481   0.000000   
2624        0                 0                3        1.155727   0.000000   
2625        0                 0                4        1.359623   0.000000   
2626        0                 0                6        1.670186   0.000000   
2627        0                 0               10        2.192972   0.000000   

          UPPER  
0     37.184272  
1     37.184272  
2     37.184272  
3     37.184272  
4     37.184272  
...         ...  
2623   0.000000  
2624   0.000000  
2625   0.000000  
2626   0.000000  
2627   0.000000  

[2628 rows x 10 columns]

In [126]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Suppose you have a DataFrame called "df" with the data

# Get a list of unique values for DIAGNOSIS_CATEGORY, AGE_CLASS, and RSS_DURATION_CLASS
diagnosis_categories = df['DIAGNOSIS_CATEGORY'].unique()
age_classes = df['AGE_CLASS'].unique()
rss_durations = df['RSS_DURATION_CLASS'].unique()

# Create subplots for all possible combinations
num_plots = len(diagnosis_categories) * len(age_classes) * len(rss_durations)
fig, axes = plt.subplots(num_plots, figsize=(10, 6*num_plots))

# Iterate through all possible combinations of DIAGNOSIS_CATEGORY, AGE_CLASS, and RSS_DURATION_CLASS
plot_index = 0
for diagnosis_category in diagnosis_categories:
    for age_class in age_classes:
        for rss_duration in rss_durations:
            subset = df[(df['DIAGNOSIS_CATEGORY'] == diagnosis_category) &
                        (df['AGE_CLASS'] == age_class) &
                        (df['RSS_DURATION_CLASS'] == rss_duration)]

            ax = axes[plot_index]

            # Plot red points for N_CASES values
            ax.scatter(subset['WEEK_LABEL'], subset['N_CASES'], c='red', label='N_CASES', marker='o')

            # Plot a blue line for BASELINE_N_CASES
            ax.plot(subset['WEEK_LABEL'], subset['BASELINE_N_CASES'], c='blue', label='BASELINE_N_CASES')

            # Plot a blue shaded area for confidence intervals
            ax.fill_between(subset['WEEK_LABEL'], subset['LOWER'], subset['UPPER'], color='blue', alpha=0.3, label='Confidence Interval')

            ax.set_title(f'Diagnosis: {diagnosis_category}, Age Class: {age_class}, RSS Duration: {rss_duration}')
            ax.set_xlabel('Week')
            ax.set_ylabel('Number of Cases')
            
            # Force the y-axis to start at zero
            ax.set_ylim(0)
            
            # Rotate the week labels for better readability
            ax.tick_params(axis='x', rotation=45)
            
            ax.legend(loc='upper left')

            plot_index += 1

# Adjust the layout of subplots to avoid overlap
plt.tight_layout()

# Display the plots
plt.show()


